## 2. Fetch the "World Development Indicators" dataset to the local file system

In [ ]:
%sh
# We switch to the root directory of our driver node
cd /
# We create a directory called input_wb_data and move into it
mkdir input_wb_data
cd input_wb_data
# We create a variable for the URL from which we'll fetch the data file
DATA_URL='https://databank.worldbank.org/data/download/WDI_csv.zip'
# We use the wget command to fetch the data
wget -O world_development_indicators.zip $DATA_URL
# We unzip the compressed file we received to extract the CSV files
unzip world_development_indicators.zip
rm world_development_indicators.zip

--2024-03-14 23:01:09--  https://databank.worldbank.org/data/download/WDI_csv.zip
Resolving databank.worldbank.org (databank.worldbank.org)... 104.18.42.231, 172.64.145.25, 2606:4700:4400::ac40:9119, ...
Connecting to databank.worldbank.org (databank.worldbank.org)|104.18.42.231|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://databankfiles.worldbank.org/public/ddpext_download/WDI_csv.zip [following]
--2024-03-14 23:01:10--  https://databankfiles.worldbank.org/public/ddpext_download/WDI_csv.zip
Resolving databankfiles.worldbank.org (databankfiles.worldbank.org)... 13.107.213.42, 13.107.246.42, 2620:1ec:bdf::42, ...
Connecting to databankfiles.worldbank.org (databankfiles.worldbank.org)|13.107.213.42|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 73436470 (70M) [application/x-zip-compressed]
Saving to: ‘world_development_indicators.zip’

     0K .......... .......... .......... .......... ..........  0%  553K 2

Archive:  world_development_indicators.zip
  inflating: WDIData.csv             
  inflating: WDICountry.csv          
  inflating: WDISeries.csv           
  inflating: WDICountry-Series.csv   
  inflating: WDISeries-Time.csv      
  inflating: WDIFootNote.csv         


In [ ]:
ls /input_wb_data/

WDICountry-Series.csv  WDIData.csv      WDISeries-Time.csv
WDICountry.csv         WDIFootNote.csv  WDISeries.csv


## 3. Move the different CSV files into the data lake’s raw directory 

In [ ]:
from datetime import datetime

# Current date in YYYYMMDD format
current_date = datetime.now().strftime("%Y%m%d")

# Directory path
directory_path = f"/datalake/raw/world_development_indicators/date={current_date}/"

# Create the directory in DBFS
dbutils.fs.mkdirs(directory_path)

csv_files = dbutils.fs.ls("file:/input_wb_data/")

for file in csv_files:
    if file.name.endswith('.csv'):
        source_path = file.path
        destination_path = directory_path + file.name
        dbutils.fs.mv(source_path, destination_path)

# List files in the target directory to confirm the move
display(dbutils.fs.ls(directory_path))

path name size modificationTime dbfs:/datalake/raw/world_development_indicators/date=20240314/WDICountry-Series.csv WDICountry-Series.csv 1054124 1710457298000 dbfs:/datalake/raw/world_development_indicators/date=20240314/WDICountry.csv WDICountry.csv 157369 1710457298000 dbfs:/datalake/raw/world_development_indicators/date=20240314/WDIData.csv WDIData.csv 218787080 1710457294000 dbfs:/datalake/raw/world_development_indicators/date=20240314/WDIFootNote.csv WDIFootNote.csv 68811925 1710457297000 dbfs:/datalake/raw/world_development_indicators/date=20240314/WDISeries-Time.csv WDISeries-Time.csv 14917 1710457294000 dbfs:/datalake/raw/world_development_indicators/date=20240314/WDISeries.csv WDISeries.csv 3999755 1710457294000

## 4. Fetch the CO2 emissions from passenger cars dataset

In [ ]:

%sh
 apt-get install jq
 cd /
 mkdir eea_input_data
 cd eea_input_data/
 BASE_URL="https://discodata.eea.europa.eu"
 TABLE="CO2Emission.latest.co2cars"
 ORDER="order%20by%20emissions%20desc"
 for YEAR in 2017 2018 2019
 do
      CONDITION="year%20%3D%20$YEAR"
      SQL_QUERY="SELECT%20*%2C%20%22Enedc%20(g%2Fkm)%22%20as%20emissions%20FROM%20$TABLE%20WHERE%20$CONDITION%20$ORDER"
      FULL_URL="$BASE_URL/sql?query=$SQL_QUERY&p=1&nrOfHits=100000"
      curl $FULL_URL | jq '.results' > co2_emissions_passenger_cars_$YEAR.json
 done

Reading package lists...
Building dependency tree...
Reading state information...
The following NEW packages will be installed:
  jq
0 upgraded, 1 newly installed, 0 to remove and 41 not upgraded.
Need to get 52.5 kB of archives.
After this operation, 102 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/main amd64 jq amd64 1.6-2.1ubuntu3 [52.5 kB]


debconf: delaying package configuration, since apt-utils is not installed


Fetched 52.5 kB in 0s (852 kB/s)
Selecting previously unselected package jq.
(Reading database ... 91195 files and directories currently installed.)
Preparing to unpack .../jq_1.6-2.1ubuntu3_amd64.deb ...
Unpacking jq (1.6-2.1ubuntu3) ...
Setting up jq (1.6-2.1ubuntu3) ...
Processing triggers for man-db (2.10.2-1) ...


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 59.6M  100 59.6M    0     0  7113k      0  0:00:08  0:00:08 --:--:-- 13.6M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 59.8M  100 59.8M    0     0  6843k      0  0:00:08  0:00:08 --:--:-- 16.2M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 61.1M  100 61.1M    0     0  6829k      0  0:00:09  0:00:09 --:--:-- 15.5M


In [ ]:
%sh
ls /eea_input_data/

co2_emissions_passenger_cars_2017.json
co2_emissions_passenger_cars_2018.json
co2_emissions_passenger_cars_2019.json


## 5.  Move the different JSON files into the data lake’s raw directory 

In [ ]:
from datetime import datetime

# Current date in YYYY format
#current_date = datetime.now().strftime("%Y")

json_files = dbutils.fs.ls("file:/eea_input_data/")

for file in json_files:
    if file.name.endswith('.json'):
        source_path = file.path
        year_file = file.name[-9:-5]
       
        # Directory path
        directory_path = f"/datalake/raw/co2_passenger_cars_emissions/year={year_file}/"

        # Create the directory in DBFS
        dbutils.fs.mkdirs(directory_path)

        destination_path = directory_path + file.name
        dbutils.fs.mv(source_path, destination_path)

# List files in the target directory to confirm the move
display(dbutils.fs.ls(directory_path))

path name size modificationTime dbfs:/datalake/raw/co2_passenger_cars_emissions/year=2018/co2_emissions_passenger_cars_2018.json co2_emissions_passenger_cars_2018.json 87675091 1710457341000

## 5. Use Apache Spark to read the two datasets

In [ ]:
df_world = spark.read.format("csv").option("header", "true").load("dbfs:/datalake/raw/world_development_indicators/date=20240313/WDIData.csv")
display(df_world)

Country Name Country Code Indicator Name Indicator Code 1960 1961 1962 1963 1964 1965 1966 1967 1968 1969 1970 1971 1972 1973 1974 1975 1976 1977 1978 1979 1980 1981 1982 1983 1984 1985 1986 1987 1988 1989 1990 1991 1992 1993 1994 1995 1996 1997 1998 1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020 2021 2022 _c67 Africa Eastern and Southern AFE Access to clean fuels and technologies for cooking (% of population) EG.CFT.ACCS.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 11.5803658833288 11.9079425294377 12.2851752012446 12.6076412016211 12.990589368338 13.3944040634838 13.8352545545734 14.2571197946687 14.687203312201 15.1241124592143 15.5452136820546 16.0286771765974 16.447498712171 16.9146250084891 17.3923491766017 17.8920045785891 18.3599925639738 18.7951511858057 19.2951759160947 19.7881558225926 20.2795987854143 20.7736266715633 null null Africa Eastern and Southern AFE Access to clean fuels and technologies for cooking, rural (% of rural population) EG.CFT.ACCS.RU.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 3.54624384950079 3.71375230244013 3.90490222403963 4.09365679549378 4.3120797561399 4.53043520417577 4.75964066633334 5.00414504385387 5.23758052815317 5.48348056189574 5.73385441202071 5.95751373846406 6.22427564223531 6.47330052280147 6.72033082192565 7.01591671529373 7.28139009342782 7.51367314282019 7.80956551360185 8.07588857955621 8.36600966417786 8.68413651796155 null null Africa Eastern and Southern AFE Access to clean fuels and technologies for cooking, urban (% of urban population) EG.CFT.ACCS.UR.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 32.6044998101412 32.9641587834881 33.4096166423109 33.7914967376809 34.2204852383808 34.7274443863933 35.159518390821 35.6949836335275 36.1021883549437 36.4475825793002 36.8496476206059 37.1803138455416 37.540748812663 37.8703467737823 38.1841517136575 38.5431800240538 38.8017190398214 39.039013572783 39.323186412267 39.6438476030676 39.8948301673967 40.2138914990743 null null Africa Eastern and Southern AFE Access to electricity (% of population) EG.ELC.ACCS.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 19.9573016173253 19.9753646761679 21.576500005381 22.5292648277365 23.749531370048 23.4930127792651 25.1912206446574 26.8079371107551 25.9433160820416 26.1938952124019 27.4001102274899 28.9143483184985 31.6669278676995 31.695183470279 31.8592573426147 33.903514646918 38.8514438926569 40.1973318677545 43.0283322203821 44.3897728327672 46.2686205693929 48.1036086917626 null null Africa Eastern and Southern AFE Access to electricity, rural (% of rural population) EG.ELC.ACCS.RU.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 8.62349738713396 null null 9.76549107771651 10.9102432017627 10.4427955703514 12.5180411959847 12.5271501168806 12.9865086541341 15.5277914218334 14.4627604783022 16.1009040222933 19.3751714802833 18.6723059476993 17.6239561137036 16.5166329797999 24.5944742175144 25.3892973709915 27.0417428231018 29.1382848280998 30.9986867049528 32.7726898837157 null null Africa Eastern and Southern AFE Access to electricity, urban (% of urban population) EG.ELC.ACCS.UR.ZS null null null null null null null null null null null null null nu

In [ ]:
df_world_data = spark.read.format("csv")\
.option("header", "true")\
    .option("delimiter", ",")\
    .load(f"dbfs:/datalake/raw/world_development_indicators/date={current_date}/WDIData.csv")

In [ ]:
#from pyspark.sql.types import *
input_path = "/datalake/raw/co2_passenger_cars_emissions"
df_co2_emissions = spark.read.option("multiline", "true").json(input_path)


## 7. a) Schema

In [ ]:
df_world.printSchema()

root
 |-- Country Name: string (nullable = true)
 |-- Country Code: string (nullable = true)
 |-- Indicator Name: string (nullable = true)
 |-- Indicator Code: string (nullable = true)
 |-- 1960: string (nullable = true)
 |-- 1961: string (nullable = true)
 |-- 1962: string (nullable = true)
 |-- 1963: string (nullable = true)
 |-- 1964: string (nullable = true)
 |-- 1965: string (nullable = true)
 |-- 1966: string (nullable = true)
 |-- 1967: string (nullable = true)
 |-- 1968: string (nullable = true)
 |-- 1969: string (nullable = true)
 |-- 1970: string (nullable = true)
 |-- 1971: string (nullable = true)
 |-- 1972: string (nullable = true)
 |-- 1973: string (nullable = true)
 |-- 1974: string (nullable = true)
 |-- 1975: string (nullable = true)
 |-- 1976: string (nullable = true)
 |-- 1977: string (nullable = true)
 |-- 1978: string (nullable = true)
 |-- 1979: string (nullable = true)
 |-- 1980: string (nullable = true)
 |-- 1981: string (nullable = true)
 |-- 1982: string (null

In [ ]:
df_co2_emissions.printSchema()

root
 |-- At1 (mm): long (nullable = true)
 |-- At2 (mm): long (nullable = true)
 |-- Cn: string (nullable = true)
 |-- Cr: string (nullable = true)
 |-- Ct: string (nullable = true)
 |-- De: double (nullable = true)
 |-- Dr: string (nullable = true)
 |-- E (g/km): string (nullable = true)
 |-- Ec (cm3): long (nullable = true)
 |-- Enedc (g/km): long (nullable = true)
 |-- Ep (KW): long (nullable = true)
 |-- Er (g/km): string (nullable = true)
 |-- Ernedc (g/km): double (nullable = true)
 |-- Erwltp (g/km): double (nullable = true)
 |-- Ewltp (g/km): long (nullable = true)
 |-- Fc: string (nullable = true)
 |-- Fm: string (nullable = true)
 |-- Ft: string (nullable = true)
 |-- ID: long (nullable = true)
 |-- IT: string (nullable = true)
 |-- M (kg): long (nullable = true)
 |-- MMS: string (nullable = true)
 |-- MS: string (nullable = true)
 |-- Man: string (nullable = true)
 |-- Mh: string (nullable = true)
 |-- Mk: string (nullable = true)
 |-- Mp: string (nullable = true)
 |-- Mt: 

## 7. b) Statistics

In [ ]:
display(df_world.describe())

summary Country Name Country Code Indicator Name Indicator Code 1960 1961 1962 1963 1964 1965 1966 1967 1968 1969 1970 1971 1972 1973 1974 1975 1976 1977 1978 1979 1980 1981 1982 1983 1984 1985 1986 1987 1988 1989 1990 1991 1992 1993 1994 1995 1996 1997 1998 1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020 2021 2022 _c67 count 395276 395276 395276 395276 38882 44147 45329 46209 46752 48958 48960 49628 50281 51044 68400 75332 77117 77801 79214 82934 85050 87457 88216 89188 93726 95716 96073 97059 97700 99142 99915 100131 100226 101981 125486 135812 139140 141659 143911 151858 159036 152409 162444 161158 195946 182053 192018 194342 199622 211596 211967 213971 214781 216059 227155 222931 224663 221941 228962 229338 225025 221368 220008 215233 195566 166351 115040 0 mean null null null null 4.353165028310107E11 4.1037588545537726E11 4.225246009447293E11 4.324092214149786E11 4.637836821700332E11 5.0747750447191187E11 5.51620205922166E11 6.03112882832862E11 6.792608057582865E11 7.518070046319597E11 6.490752971373839E11 6.762925308371776E11 7.579659839395581E11 8.826931402752153E11 1.1774191426184053E12 1.1953625453594155E12 1.330209293346261E12 1.286831563849225E12 1.1166521031189502E12 1.05961815312937E12 8.364065551074633E11 8.045147883015282E11 8.871037918164341E11 1.1098926894734915E12 1.1315846704629167E12 1.22877222440577E12 1.1451621303153323E12 1.1555913242660146E12 8.974619572269663E11 9.731471822496166E11 1.0114414666350745E12 9.863369322411649E11 1.0043650703333068E12 1.0876148212240676E12 1.1660831063032468E12 1.1762251353861846E12 1.108988574470608E12 1.1788529651780203E12 1.0263553426480834E12 1.0562060096777977E12 9.245860713443566E11 1.040853154261332E12 1.2004533803978333E12 1.170523106679442E12 1.327571707885879E12 1.3543751854221284E12 1.5037455270019817E12 1.7789919048908967E12 1.9561653548820498E12 2.0182959850801743E12 2.257578259250597E12 2.568456151704422E12 2.6798779321837476E12 2.970408062949453E12 3.1219718537963516E12 3.1963452034549917E12 3.5700340996242803E12 3.8325109409584707E12 4.3032257586624546E12 2.98421614096548E13 4.225127890395116E14 2.6016799238106405E15 2.6823615304064116E16 null stddev null null null null 1.9810703421436086E13 2.0157324097574336E13 2.1187109943069285E13 2.2222373916682766E13 2.397489189626113E13 2.7158423106472676E13 3.006711886878044E13 3.335017217662249E13 3.783570401592148E13 4.296537860753167E13 4.117363328691135E13 4.5097557395507164E13 5.144160600465189E13 5.884441811168723E13 8.037755561360797E13 8.073604752850495E13 9.19443216146823E13 8.839623658569012E13 7.331734360853031E13 6.893018620908421E13 5.120779084827237E13 4.808626360288201E13 5.4170552055249016E13 6.708556497274905E13 7.0093618309250984E13 8.280643023104406E13 7.692551961124498E13 7.053825126738873E13 4.6844447058742445E13 5.0374340519160695E13 5.8451218644625016E13 5.76669744451728E13 5.8679884805547555E13 6.427326034352305E13 6.891360205735622E13 6.876675761655364E13 5.918676925037002E13 5.932649143772593E13 5.4968434365973805E13 5.8612918814758875E13 5.8941780651853E13 6.6552336912711266E13 6.4473639732448375E13 7.56170982561063E13 7.387024880964972E13 7.822420564721164E13 8.246474376424902E13 8.989910802169808E13 9.319890729747833E13 9.498622808148522E13 1.0531760562316931E14 1.158641687161107E14 1.1681950413768303E14 1.2791216236638458E14 1.3707945224608694E14 1.3990646546769511E14 1.5692301054492656E14 1.6933540536360097E14 1.9371169852636684E14 1.1623132094223054E16 1.8417880013607622E17 1.057422779463962E18 9.092173193463385E18 null min Afghanistan ABW ARI treatment (% of children under 5 taken to a health provider) AG.AGR.TRAC.NO -0.00330839030000001 -0.0058159009 -0.000155636363545455 -0.000243272726363636 -0.000112838000000001 -0.000641454544454546 -0.000554181818454545 -0.000876727273454545 -0.0002550001 -0.000425453699999996 -0.0002970001 -0.00064314309999999 -0.000224618999999992 -0.000459999996666664 -0.0004730224609375 -0.000168

In [ ]:
display(df_co2_emissions.describe())

summary At1 (mm) At2 (mm) Cn Cr Ct De Dr E (g/km) Ec (cm3) Enedc (g/km) Ep (KW) Er (g/km) Ernedc (g/km) Erwltp (g/km) Ewltp (g/km) Fc Fm Ft ID IT M (kg) MMS MS Man Mh Mk Mp Mt R Status T TAN VFN Va Ve Version_file Vf W (mm) year Z (Wh/km) Zr emissions count 283796 276264 299985 299092 298302 10009 0 0 299975 300000 248465 0 7155 2837 109271 0 299993 300000 300000 275347 299434 299262 299996 300000 300000 299782 300000 109747 300000 300000 299974 299872 285553 299901 299844 300000 16327 286707 300000 57 0 300000 mean 1630.9797742040057 1637.6940788521124 800.3777280320749 null null -0.0017782595663903894 null null 4193.517909825819 265.74504333333334 340.6469603364659 null 1.637302585604349 0.0190341910468805 307.6761537827969 null null null 5428304.994346667 7.285714285714286 2060.2311761523406 8.0 null null null 8.0 null 2197.4197290130937 2.3217833333333333 null 474.68976943734225 111.0 null 3.1976744186046466E90 322387.70663470967 null 0.2548539229497152 2786.198125612559 2018.0 217.24561403508773 null 265.74504333333334 stddev 57.1876011615477 53.33979711205964 948.7842391553709 null null 0.04091028064042706 null null 1161.5307516224473 46.16069680797603 107.26642344267087 null 0.3011054880652328 0.18558046935955036 35.98164437703905 null null null 3900984.1100472105 3.5326937743674747 352.7165040089179 0.0 null null null 0.0 null 518.6146858038334 22.576252961398357 null 5661.372274374247 128.17175976009693 null 3.352264964430472E91 683784.4486736971 null 0.4357924194707832 320.61966085480924 0.816497941758763 21.869973464738614 null 46.16069680797603 min 501 501 -0.078 null null 898 185 27 null 1.0 0.0 11 null 307 242 AT AA-IVA 0 1 F v15 0 0 2017 100 null 185 max 2895 2250 unknown m1 m1 2.0 null null 8382 671 1103 null 3.0 1.9 535 null P petrol/electric 15499148 e24*2 4160 ZESZUTA SK VOLVO CAR CORPORATION unknown ZENVO VW GROUP PC 4612 3250 P l50 e9*ks07/46*6716*01 RL-ZE1AEM57A6_0000-SJN-1 ZYX10(H) h v20 1 4762 2019 296 null 671

## 7. c) Number of records

In [ ]:


print(f'Number of records  for World Development Indicators DataFrame is: {df_world.count()}')


Number of records  for World Development Indicators DataFrame is: 395276


In [ ]:
print(f"Number of records  of CO2 Emissions DataFrame is: {df_co2_emissions.count()}")

Number of records  of CO2 Emissions DataFrame is: 300000


## 7. d) Sample from the two datasets

In [ ]:
display(df_world.sample(fraction=0.00001))

Country Name Country Code Indicator Name Indicator Code 1960 1961 1962 1963 1964 1965 1966 1967 1968 1969 1970 1971 1972 1973 1974 1975 1976 1977 1978 1979 1980 1981 1982 1983 1984 1985 1986 1987 1988 1989 1990 1991 1992 1993 1994 1995 1996 1997 1998 1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020 2021 2022 _c67 Cyprus CYP Adjusted savings: mineral depletion (current US$) NY.ADJ.DMIN.CD null null null null null null null null null null 10190113.1616984 6373649.80845472 5962953.94497045 10350492.1431835 9864318.1123715 3127978.93552354 4051772.15095905 1927653.64587632 1535004.86502435 693716.862188629 761017.931211332 0 205838.53154384 404865.14863129 295362.216541707 281979.92064392 89068.8243458013 32053.9679541438 221139.364036438 612571.36093426 367614.366548224 72241.1197017051 72423.0823507301 44405.4311671528 0 0 392690.527661548 964071.21907391 421822.875595412 576412.479230363 948081.822953723 422300.318840657 557858.879095043 492944.73131785 741398.709233644 0 0 628091.093019088 468001.607844664 2503310.47893927 4946712.74485517 8608124.99381906 7347577.61801209 4703287.02775891 3538403.40083868 1798120.80512297 0 722472.474336169 763563.229253612 580738.114374684 1314665.16375144 2623796.31934394 null null India IND Time required to obtain an operating license (days) IC.FRM.DURS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 17.8 null null null null null null null 23.8 null Lesotho LSO Voice and Accountability: Percentile Rank, Upper Bound of 90% Confidence Interval VA.PER.RNK.UPPER null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 50 null 48.756217956543 null 51.7412948608398 null 60.6965179443359 60.1990051269531 56.25 54.3269233703613 59.1346168518066 54.8076934814453 52.4038467407227 54.028434753418 54.028434753418 53.9906120300293 57.2769966125488 57.7464790344238 59.6059112548828 58.6206893920898 53.694580078125 54.1871910095215 55.8252410888672 53.1400947570801 53.6231880187988 54.5893707275391 55.5555572509766 null Turkmenistan TKM Claims on central government, etc. (% GDP) FS.AST.CGOV.GD.ZS null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null

In [ ]:
display(df_co2_emissions.sample(fraction=0.00001))

At1 (mm) At2 (mm) Cn Cr Ct De Dr E (g/km) Ec (cm3) Enedc (g/km) Ep (KW) Er (g/km) Ernedc (g/km) Erwltp (g/km) Ewltp (g/km) Fc Fm Ft ID IT M (kg) MMS MS Man Mh Mk Mp Mt R Status T TAN VFN Va Ve Version_file Vf W (mm) year Z (Wh/km) Zr emissions 1684 1651 AMG GT S M1 M1 null null null 3982 262 384 null null null 278 null M petrol 7303603 1700 MERCEDES-AMG DE MERCEDES-AMG GMBH MERCEDES AMG MERCEDES-AMG DAIMLER AG 1787 1 P 197 E1*2007/46*0233*15 Z48ST0 1ZAA020A v19 null 2630 2019 null null 262 1690 1683 R ROVER SVA-BIO DYN V8 SC A M1G M1G null null null 4999 298 415 null null null null null M Petrol 3250580 2524 LAND ROVER GB JAGUAR LAND ROVER LIMITED JAGUAR LAND ROVER LIMITED LAND ROVER TATA MOTORS JAGUAR LAND ROVER null 1 F LG e11*2007/46*0649*21 IP-09-SAL-2018-0050 S5IT2K D5IA v18 null 2922 2018 null null 298 1572 1572 WRANGLER UNLIMITED M1 M1G null null null 3604 273 209 null null null null null M Petrol 508482 1995 FCA US LLC FR FCA US LLC CHRYSLER JEEP FCA ITALY SPA null 1 F JK e4*2001/116*0116*23 JXJFX H5HN3A v18 null 2947 2018 null null 273 1634 1631 S600 MAYBACH AUTO M1 null null null 5980 274 null null null null null null M petrol 423386 2335 MERCEDES GB DAIMLER AG DAIMLER AG MERCEDES DAIMLER AG null 1 F 221 e1*2001/116*0335*32 P97BP0 NZAA0502 v16 null 3365 2017 null null 274 1665 1705 AMG GLE 43 M1 M1 null null null 2996 209 270 null null null null null M Petrol 945186 2240 MERCEDES BE DAIMLER AG DAIMLER AG Mercedes-Benz DAIMLER AG null 1 F 166 E1*2007/46*0598*19 A35HP1 CZAAA502 v16 null 2915 2017 null null 209

In [4]:
import requests
import os
import json

# Create the directory for data
data_dir = "/eea_input_data"
os.makedirs(data_dir, exist_ok=True)

# Define the base URL and other constants
BASE_URL = "https://discodata.eea.europa.eu"
TABLE = "CO2Emission.latest.co2cars"
ORDER = "order by emissions desc"

# Loop through the specified years
for YEAR in [2020]:
    CONDITION = f"year = {YEAR}"
    COLUMNS = "*%2C cast(%22Enedc (g%2Fkm)%22 as emissions) * 1.1 as %22Enedc (g%2Fkm) V2%22"
    SQL_QUERY = f"SELECT {COLUMNS} FROM {TABLE} WHERE {CONDITION} {ORDER}"
    FULL_URL = f"{BASE_URL}/sql?query={SQL_QUERY}&p=1&nrOfHits=100000"
    
    # Make the HTTP GET request
    response = requests.get(FULL_URL)
    
    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()['results']  # Assuming 'results' is the key containing the data
        file_path = os.path.join(data_dir, f"co2_emissions_passenger_cars_{YEAR}.json")
        
        # Save the data to a JSON file
        with open(file_path, 'w') as f:
            json.dump(data, f)
    else:
        print(f"Failed to fetch data for {YEAR}: HTTP {response.status_code}")

Failed to fetch data for 2020: HTTP 403


In [2]:
import requests
import os
import json

data_dir = "eea_input_data"
os.makedirs(data_dir, exist_ok=True)

BASE_URL = "https://discodata.eea.europa.eu"
TABLE = "CO2Emission.latest.co2cars"
ORDER = "order by emissions desc"

headers = {
    'User-Agent': 'Mozilla/5.0'
}

for YEAR in [2017, 2018, 2019]:
    CONDITION = f"year = {YEAR}"
    COLUMNS = "*%2C cast(%22Enedc (g%2Fkm)%22 as float) * 1.1 as %22Enedc (g%2Fkm) V2%22"
    SQL_QUERY = f"SELECT {COLUMNS} FROM {TABLE} WHERE {CONDITION} {ORDER}"
    FULL_URL = f"{BASE_URL}/sql?query={SQL_QUERY}&p=1&nrOfHits=100000"
    
    response = requests.get(FULL_URL, headers=headers)
    
    if response.status_code == 200:
        data = response.json()['results']
        file_path = os.path.join(data_dir, f"co2_emissions_passenger_cars_{YEAR}.json")
        
        with open(file_path, 'w') as f:
            json.dump(data, f)
    else:
        print(f"Failed to fetch data for {YEAR}: HTTP {response.status_code}")

Failed to fetch data for 2017: HTTP 403
Failed to fetch data for 2018: HTTP 403
Failed to fetch data for 2019: HTTP 403
